In [2]:
%matplotlib inline
import bisect
import copy 
import os 
from collections import deque, Counter
import random
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import editdistance
import sys
import RNA
from typing import Dict, List, Tuple

# import path 
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

from utils.sequence_utils import translate_one_hot_to_string,generate_random_mutant
from utils.sequence_utils import translate_string_to_one_hot, translate_one_hot_to_string
from models.Theoretical_models import *
from models.Noise_wrapper import *
from utils.landscape_utils import *
from models.RNA_landscapes import *
from models.Multi_dimensional_model import *

import tensorflow as tf
from tf_agents.drivers import dynamic_step_driver
from tf_agents.metrics import tf_metrics
from tf_agents.agents import tf_agent
from tf_agents.policies import random_tf_policy
from tf_agents.agents.ppo import ppo_policy, ppo_agent, ppo_utils
from tf_agents.environments import py_environment, tf_py_environment
from tf_agents.environments.utils import validate_py_environment
from tf_agents.drivers import dynamic_episode_driver
from tf_agents.networks import network, normal_projection_network
from tf_agents.replay_buffers import tf_uniform_replay_buffer
from tf_agents.utils import common
from tf_agents.trajectories import time_step as ts
from tf_agents.specs import array_spec

In [2]:
RAA="UGCA" #alphabet
alphabet_len=len(RAA)
# TODO: UNDO THIS
# length=40
length=40
noise_alpha=1
generations = 10
experiment_batch_size = 1000
wt=generate_random_sequences(length,1,alphabet=RAA)[0]
landscape1=RNA_landscape(wt)
landscape2=RNA_landscape(wt)
noisy_landscape=Noise_wrapper(landscape1,
                              noise_alpha=noise_alpha,
                              always_costly=True)
initial_genotypes=list(set([wt]+[generate_random_mutant(wt,0.05,RAA) 
                                 for i in range(experiment_batch_size*10)]))[:experiment_batch_size]
noisy_landscape.reset()
noisy_landscape.measure_true_landscape(initial_genotypes)
noisy_landscape.natural_mode=False
noisy_landscape.local_mode=False
noisy_landscape.cost

def renormalize_moves(one_hot_input, rewards_output):
    """ensures that staying in place gives no reward"""
    zero_current_state = (one_hot_input - 1) * (-1)
    return np.multiply(rewards_output, zero_current_state)

def walk_away_renormalize_moves(one_hot_input, one_hot_wt, rewards_output):
    """ensures that moving toward wt is also not useful"""
    zero_current_state=(one_hot_input-1)*-1
    zero_wt=((one_hot_wt-1)*-1)
    zero_conservative_moves=np.multiply(zero_wt,zero_current_state)
    return np.multiply(rewards_output,zero_conservative_moves)

def get_all_singles_fitness(model,sequence,alphabet):
    prob_singles=np.zeros((len(alphabet),len(sequence)))
    for i in range(len(sequence)):
        for j in range(len(alphabet)):
            putative_seq=sequence[:i]+alphabet[j]+sequence[i+1:]
           # print (putative_seq)
            prob_singles[j][i]=model.get_fitness(putative_seq)
    return prob_singles

def get_all_mutants(sequence):
    mutants = []
    for i in range(sequence.shape[0]):
        for j in range(sequence.shape[1]):
            putative_seq = sequence.copy()
            putative_seq[:, j] = 0
            putative_seq[i, j] = 1
            mutants.append(putative_seq)
    return np.array(mutants)

def sample_greedy(matrix):
    i,j=matrix.shape
    max_arg=np.argmax(matrix)
    y=max_arg%j
    x=int(max_arg/j)
    output=np.zeros((i,j))
    output[x][y]=matrix[x][y]
    return output

def sample_multi_greedy(matrix):
    n = 5 # the number of base positions to greedily change
    max_args = np.argpartition(matrix.flatten(), -n)[-n:]
    i,j=matrix.shape
    output=np.zeros((i,j))
    for max_arg in max_args:
        y=max_arg%j
        x=int(max_arg/j)
        output[x][y]=matrix[x][y]
    return output

def sample_random(matrix):
    i,j=matrix.shape
    non_zero_moves=np.nonzero(matrix)
   # print (non_zero_moves)
    k=len(non_zero_moves)
    l=len(non_zero_moves[0])
    if k!=0 and l!=0:
        rand_arg=random.choice([[non_zero_moves[alph][pos] for alph in range(k)] for pos in range(l)])
    else:
        rand_arg=[random.randint(0,i-1),random.randint(0,j-1)]
    #print (rand_arg)
    y=rand_arg[1]
    x=rand_arg[0]
    output=np.zeros((i,j))
    output[x][y] = 1
    return output   

def action_to_scalar(matrix):
    matrix = matrix.ravel()
    for i in range(len(matrix)):
        if matrix[i] != 0:
            return i
    
def construct_mutant_from_sample(pwm_sample, one_hot_base):
    one_hot = np.zeros(one_hot_base.shape)
    one_hot += one_hot_base
    nonzero = np.nonzero(pwm_sample)
    nonzero = list(zip(nonzero[0], nonzero[1]))
    for nz in nonzero: # this can be problematic for non-positive fitnesses
        i, j = nz
        one_hot[:,j]=0
        one_hot[i,j]=1
    return one_hot

def best_predicted_new_gen(actor, genotypes, alphabet, pop_size):
    mutants = get_all_mutants(genotypes)
    one_hot_mutants = np.array([translate_string_to_one_hot(mutant, alphabet) for mutant in mutants])
    torch_one_hot_mutants = torch.from_numpy(np.expand_dims(one_hot_mutants, axis=0)).float()
    predictions = actor(torch_one_hot_mutants)
    predictions = predictions.detach().numpy()
    best_pred_ind = predictions.argsort()[-pop_size:]
    return mutants[best_pred_ind]

def make_one_hot_train_test(genotypes, model, alphabet):
    genotypes_one_hot = np.array([translate_string_to_one_hot(genotype, alphabet) for genotype in genotypes])
    genotype_fitnesses = []
    for genotype in genotypes:
        genotype_fitnesses.append(model.get_fitness(genotype))
    genotype_fitnesses = np.array(genotype_fitnesses)

    return genotypes_one_hot, genotype_fitnesses

In [3]:
# parameters for PPO Agent 
generations = 10
experiment_batch_size = 1000
global_step = tf.compat.v1.train.get_or_create_global_step()
optimizer = tf.keras.optimizers.Adam(1e-3)
optimizer.iterations = global_step

In [4]:
# environment for PPO Agent
class FitnessLandscapeEnvironment(py_environment.PyEnvironment):
    # Based on this: https://www.mikulskibartosz.name/how-to-create-an-environment-for-a-tensorflow-agent/
    def __init__(self, alphabet, seq_len, landscape, max_episodes):
        self.alphabet = alphabet
        self.alphabet_len = len(self.alphabet)
        self.landscape = copy.deepcopy(landscape)
        self.seq_len = seq_len
        self._action_spec = array_spec.BoundedArraySpec(
            shape=(1, 2), dtype=np.float32, minimum=0, 
            maximum=1, name='action_x')
        self._observation_spec = array_spec.BoundedArraySpec(
            shape=(self.alphabet_len, self.seq_len), dtype=np.float32, minimum=0, 
            maximum=1, name='observation')
        self._time_step_spec = ts.time_step_spec(self._observation_spec)
        self._state = translate_string_to_one_hot(wt, self.alphabet)
        self._episode_ended = False
        self.ctr = 0
        self.max_episodes = max_episodes
        self.seen_sequences = {}
        
    def _reset(self):
        self.ctr = 0
        # TODO: UNDO THIS
#         self._state = translate_string_to_one_hot(wt, self.alphabet)
        self._state = translate_string_to_one_hot(generate_random_sequences(length,1,alphabet=RAA)[0], self.alphabet)
        self._episode_ended = False
        return ts.restart(np.array(self._state, dtype=np.float32))
    
    def time_step_spec(self):
        return self._time_step_spec 

    def action_spec(self):
        return self._action_spec

    def observation_spec(self):
        return self._observation_spec
    
    def get_state_string(self):
        return translate_one_hot_to_string(self._state, self.alphabet)
    
    def _step(self, action):
        if self.ctr < self.max_episodes:
            self.ctr += 1
            action_one_hot = np.zeros((self.alphabet_len, self.seq_len))
            print('action', action)
            x, y = action[0]
            x, y = int(self.alphabet_len*x), int(self.seq_len*y)
            action_one_hot[x, y] = 1
            assert self._state.sum() == self._state.shape[1]
            if self._state[x, y] == 1:
                self._episode_ended = True
                return ts.termination(np.array(self._state, dtype=np.float32), 0)
            else:
                self._state = construct_mutant_from_sample(action_one_hot, self._state)
                state_string = translate_one_hot_to_string(self._state, self.alphabet)
                
                if state_string in self.seen_sequences:
                    return ts.termination(np.array(self._state, dtype=np.float32), 0)
                self.seen_sequences[state_string] = 1
                
                reward = self.landscape.get_fitness(state_string)
                assert self._state.sum() == self._state.shape[1]
                print('New state', self._state)
                return ts.transition(np.array(self._state, dtype=np.float32), reward=reward)
        else:
            self._episode_ended = True
            assert self._state.sum() == self._state.shape[1]
            print('New state', self._state)
            return ts.termination(np.array(self._state, dtype=np.float32), 0)

In [5]:
#max_iter = experiment_batch_size * generations 
max_iter = 10 ** 6
fle2 = FitnessLandscapeEnvironment(RAA, length, landscape1, max_iter)
print("starting validating environment...")
validate_py_environment(fle2, episodes=2)
print("done validating environment.")
fle = FitnessLandscapeEnvironment(RAA, length, landscape2, max_iter)
tf_env = tf_py_environment.TFPyEnvironment(fle)

starting validating environment...
action [[0.2680582  0.78098875]]
New state [[1. 0. 1. 1. 0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0.
  1. 0. 0. 1. 0. 1. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 1. 0. 0. 1. 0. 1. 0. 1.
  0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0.
  0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 1. 1. 0.]]
action [[0.87408054 0.7873583 ]]
New state [[1. 0. 1. 1. 0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0.
  1. 0. 0. 1. 0. 1. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 1. 0. 0. 1. 0. 1. 0. 1.
  0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0.]
 [0

In [6]:
# specs 
time_step_spec = tf_env.time_step_spec()
observation_spec = tf_env.observation_spec()
action_spec = tf_env.action_spec()
alphabet_len = len(RAA)
seq_len = length

In [7]:
# run random agent for testing purposes only 
random_policy = random_tf_policy.RandomTFPolicy(tf_env.time_step_spec(), tf_env.action_spec())
random_collect_policy = random_tf_policy.RandomTFPolicy(tf_env.time_step_spec(), tf_env.action_spec())
random_agent = tf_agent.TFAgent(
    tf_env.time_step_spec(),
    tf_env.action_spec(),
    random_policy,
    random_collect_policy,
    None
)

collect_driver = dynamic_step_driver.DynamicStepDriver(
    tf_env,
    random_agent.collect_policy,
    num_steps=1000
)

collect_driver.run()

Instructions for updating:
SeedStream has moved to `tfp.util.SeedStream`.
action [[0.9681208  0.89113593]]
New state [[1. 0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1.
  0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 0. 0.
  0. 1. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 0. 1. 1. 1.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 1. 0.
  1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0.]]
action [[0.9711348  0.85397613]]
New state [[1. 0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1.
  0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 0. 0.
  0. 1. 0. 0. 1

  0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0.]]
action [[0.519887   0.37943506]]
New state [[0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0.
  1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 1. 1. 0. 1. 0. 1. 1. 0. 0. 1. 0.
  0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 1. 0. 1. 0. 0.]
 [1. 1. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1.
  0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0.]]
action [[0.54694104 0.47810423]]
New state [[0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0.
  1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 1. 1. 0. 1. 0. 1. 0. 0. 0. 1. 0.
  0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 1. 0. 1. 0. 0.]
 [1. 1. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0.
  0. 1. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0.

New state [[0. 0. 1. 1. 0. 1. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 1.
  0. 0. 0. 1. 0. 0. 0. 1. 1. 1. 0. 0. 0. 1. 1. 0.]
 [1. 0. 0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0.
  0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 1. 0. 1. 1. 1. 0. 0. 0. 0.
  0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1.]
 [0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0.]]
action [[0.29641128 0.13505507]]
New state [[0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 1.
  0. 0. 0. 1. 0. 0. 0. 1. 1. 1. 0. 0. 0. 1. 1. 0.]
 [1. 0. 0. 0. 0. 1. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0.
  0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 1. 0. 1. 1. 1. 0. 0. 0. 0.
  0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1.]
 [0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 

New state [[0. 1. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 1. 1. 1. 1. 0. 1. 1. 1. 0. 0. 0. 1.
  1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1.]
 [0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0.
  0. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]]
action [[0.409173   0.27424252]]
New state [[0. 1. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 1. 1. 1. 1. 0. 1. 1. 1. 0. 0. 0. 1.
  1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1.]
 [0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 

  0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]]
action [[0.6051749  0.70576644]]
action [[0.01469874 0.5065607 ]]
New state [[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 1. 0. 0. 0.
  1. 0. 0. 1. 0. 0. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0.]
 [1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 1.
  0. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0.]
 [0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0.
  0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]]
action [[0.5699457 0.1313194]]
action [[0.6166179  0.93451905]]
New state [[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 1. 0. 0. 0.
  1. 0. 0. 1. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0.]
 [1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 

...

action [[0.6447654 0.9815345]]
New state [[0. 0. 0. 1. 1. 1. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 1. 1. 0.
  0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 1. 0. 0. 1. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 0. 1.
  1. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 1. 0. 0. 1.]
 [1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0.]]
action [[0.2202748  0.61974835]]
New state [[0. 0. 0. 1. 1. 1. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 1. 1. 0.
  1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 1. 0. 0. 1. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 0. 1.
  0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 0. 1. 0. 0. 1.]
 [1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.

action [[0.9032066 0.8374044]]
New state [[0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 1.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]
 [1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 1. 0. 0. 0. 0.
  1. 0. 0. 1. 0. 1. 0. 1. 0. 0. 1. 1. 0. 1. 0. 0.]
 [0. 1. 0. 1. 1. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0.
  0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 0. 0. 1. 0. 0. 0.]]
action [[0.871801   0.33945417]]
New state [[0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 1.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]
 [1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 1. 0. 0. 0. 0.
  1. 0. 0. 1. 0. 1. 0. 1. 0. 0. 1. 1. 0. 1. 0. 0.]
 [0. 1. 0. 1. 1. 1. 0. 0. 0. 0. 0. 1. 0.

action [[0.836503   0.24868453]]
New state [[0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 1. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1.]
 [1. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0.
  1. 0. 0. 1. 0. 1. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0.]
 [0. 1. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 1. 1. 1. 1. 0. 1. 0. 0. 0. 0. 1.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0.]]
action [[0.90342176 0.04149532]]
action [[0.43966162 0.44290912]]
New state [[0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 1. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 0. 1. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1.]
 [1. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0.
  1. 0. 0. 1. 0. 1. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0.]
 [0. 

action [[0.8216853  0.44534075]]
New state [[0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0.
  0. 1. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0.
  0. 0. 1. 0. 0. 0. 0. 1. 1. 1. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.
  1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1.]
 [1. 0. 0. 1. 1. 0. 1. 0. 0. 1. 1. 0. 1. 1. 0. 0. 0. 1. 1. 1. 0. 0. 0. 1.
  0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0.]]
action [[0.58017313 0.32870162]]
New state [[0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0.
  0. 1. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0.
  0. 0. 1. 0. 0. 0. 0. 1. 1. 1. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.
  1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1.]
 [1. 0. 0. 1. 1. 0. 1. 0. 0. 1. 1. 0. 

(TimeStep(step_type=<tf.Tensor: id=42418, shape=(1,), dtype=int32, numpy=array([1], dtype=int32)>, reward=<tf.Tensor: id=42419, shape=(1,), dtype=float32, numpy=array([0.05058824], dtype=float32)>, discount=<tf.Tensor: id=42420, shape=(1,), dtype=float32, numpy=array([1.], dtype=float32)>, observation=<tf.Tensor: id=42421, shape=(1, 4, 40), dtype=float32, numpy=
 array([[[1., 1., 1., 0., 1., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.,
          0., 0., 0., 1., 1., 0., 1., 1.],
         [0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 1.,
          1., 0., 0., 0., 0., 1., 0., 0., 0., 0., 1., 0., 0., 0., 0., 1.,
          1., 1., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 1., 0., 0., 1., 0., 1., 1., 1., 1., 1., 0.,
          0., 0., 0., 1., 0., 0., 1., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 1., 0., 0., 1., 0., 0., 0., 0., 0., 0., 

In [8]:
# https://github.com/Yawmus/MachineLearning/blob/32c7b7b5ee853fd188d1c22112ba16f031202a0d/rl/main.py
from tf_agents.utils import nest_utils
from tf_agents.networks import encoding_network
from tf_agents.networks import actor_distribution_network
from tf_agents.networks import value_network

# https://gist.github.com/Ujwal2910/885bc6f32ca4719d1cdd4fbd427b835e
# https://github.com/tensorflow/agents/blob/master/tf_agents/networks/normal_projection_network.pyd
print('action_spec', action_spec)
def normal_projection_net(action_spec, init_means_output_factor=0.1):
      return normal_projection_network.NormalProjectionNetwork(
          action_spec,
          init_means_output_factor=init_means_output_factor,
          state_dependent_std=True,
          scale_distribution=True)
      '''
      return normal_projection_network.NormalProjectionNetwork(
          action_spec,
          activation_fn=tf.nn.softmax,
          mean_transform=None,
          state_dependent_std=True,
          init_means_output_factor=init_means_output_factor,
          scale_distribution=True)
      '''

class ActorNet(network.DistributionNetwork):
    def __init__(self, input_tensor_spec, output_tensor_spec): 
        projection_networks = tf.nest.map_structure(normal_projection_net, 
                                                    output_tensor_spec)
        output_spec = tf.nest.map_structure(lambda proj_net: proj_net.output_spec,
                                            projection_networks)
        super(ActorNet, self).__init__(
            input_tensor_spec,
            (),
            output_spec,
            'ActorNet')
        self._projection_networks = projection_networks 
        self._output_tensor_spec = output_tensor_spec
        self._layers = [
            tf.keras.layers.Flatten(),
            tf.keras.layers.Dense(seq_len, activation=tf.nn.relu),
            tf.keras.layers.Dense(5, activation=tf.nn.relu)
        ]
    
    def call(self, observations, step_type, network_state):
        print('Observations in ActorNet', observations)
        del step_type
        output = tf.keras.backend.reshape(observations, (-1, alphabet_len, seq_len))
        outer_rank = nest_utils.get_outer_rank(output, self.input_tensor_spec)
        for layer in self._layers:
            output = layer(output)
            print('Output of neural network for action', layer, output.numpy())
        output = tf.nest.map_structure(
            lambda proj_net: proj_net(output, outer_rank), self._projection_networks)
        return output, network_state


class ValueNet(network.Network):
    def __init__(self, input_tensor_spec):
        super(ValueNet, self).__init__(
            input_tensor_spec,
            (),
            'ValueNet')
        self._layers = [
            tf.keras.layers.Flatten(),
            tf.keras.layers.Dense(
                seq_len, activation=tf.nn.relu),
            tf.keras.layers.Dense(
                5, activation=tf.nn.relu),
            tf.keras.layers.Dense(
                1, activation=tf.nn.sigmoid),
        ]
        
    def call(self, observations, step_type, network_state):
        del step_type
        output = tf.keras.backend.reshape(observations, (-1, alphabet_len, seq_len))
        for layer in self._layers:
            output = layer(output)
        return tf.transpose(output), network_state
        
actor_net = ActorNet(observation_spec, action_spec)
value_net = ValueNet(observation_spec)
'''
actor_net = actor_distribution_network.ActorDistributionNetwork(
    tf_env.observation_spec(),
    tf_env.action_spec(),
    fc_layer_params=(128,),
    continuous_projection_net=normal_projection_net
)
value_net = value_network.ValueNetwork(
    tf_env.observation_spec(),
    fc_layer_params=(40, 5)
)
'''

optimizer = tf.compat.v1.train.AdamOptimizer(learning_rate=3.0e-4)

agent = ppo_agent.PPOAgent(
    tf_env.time_step_spec(),
    tf_env.action_spec(),
    optimizer,
    actor_net=actor_net,
    value_net=value_net
)

action_spec BoundedTensorSpec(shape=(1, 2), dtype=tf.float32, name='action_x', minimum=array(0., dtype=float32), maximum=array(1., dtype=float32))
Observations in ActorNet tf.Tensor([], shape=(0, 4, 40), dtype=float32)
Output of neural network for action <tensorflow.python.keras.layers.core.Flatten object at 0x7efc0824ea90> []
Output of neural network for action <tensorflow.python.keras.layers.core.Dense object at 0x7efc081ee1d0> []
Output of neural network for action <tensorflow.python.keras.layers.core.Dense object at 0x7efc081eebd0> []
Instructions for updating:
`AffineScalar` bijector is deprecated; please use `tfb.Shift(loc)(tfb.Scale(...))` instead.


In [9]:
replay_buffer = tf_uniform_replay_buffer.TFUniformReplayBuffer(
    agent.collect_data_spec,
    batch_size=1,
    max_length=2
)
collect_driver = dynamic_step_driver.DynamicStepDriver(
    tf_env,
    agent.collect_policy,
    observers=[replay_buffer.add_batch],
    num_steps=2
)

In [13]:
print('Observations', replay_buffer.gather_all())
collect_driver.run()

Observations Trajectory(step_type=<tf.Tensor: id=784311, shape=(1, 0), dtype=int32, numpy=array([], shape=(1, 0), dtype=int32)>, observation=<tf.Tensor: id=784312, shape=(1, 0, 4, 40), dtype=float32, numpy=array([], shape=(1, 0, 4, 40), dtype=float32)>, action=<tf.Tensor: id=784313, shape=(1, 0, 1, 2), dtype=float32, numpy=array([], shape=(1, 0, 1, 2), dtype=float32)>, policy_info=DictWrapper({'loc': <tf.Tensor: id=784314, shape=(1, 0, 1, 2), dtype=float32, numpy=array([], shape=(1, 0, 1, 2), dtype=float32)>, 'scale': <tf.Tensor: id=784315, shape=(1, 0, 1, 2), dtype=float32, numpy=array([], shape=(1, 0, 1, 2), dtype=float32)>}), next_step_type=<tf.Tensor: id=784316, shape=(1, 0), dtype=int32, numpy=array([], shape=(1, 0), dtype=int32)>, reward=<tf.Tensor: id=784317, shape=(1, 0), dtype=float32, numpy=array([], shape=(1, 0), dtype=float32)>, discount=<tf.Tensor: id=784318, shape=(1, 0), dtype=float32, numpy=array([], shape=(1, 0), dtype=float32)>)
Observations in ActorNet tf.Tensor(
[[[

(TimeStep(step_type=<tf.Tensor: id=784533, shape=(1,), dtype=int32, numpy=array([1], dtype=int32)>, reward=<tf.Tensor: id=784534, shape=(1,), dtype=float32, numpy=array([0.09647059], dtype=float32)>, discount=<tf.Tensor: id=784535, shape=(1,), dtype=float32, numpy=array([1.], dtype=float32)>, observation=<tf.Tensor: id=784536, shape=(1, 4, 40), dtype=float32, numpy=
 array([[[1., 0., 0., 0., 0., 0., 0., 1., 0., 1., 0., 1., 0., 0., 0., 0.,
          0., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 1., 1., 0., 0., 1.],
         [0., 1., 0., 1., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 1., 0., 0., 0., 0., 1., 1., 0., 0., 0., 1., 0., 1., 1., 1.,
          1., 0., 0., 0., 0., 0., 1., 0.],
         [0., 0., 1., 0., 1., 0., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1.,
          1., 0., 0., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.,
          0., 0., 1., 0., 0., 1., 0., 0.],
         [0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1., 0., 

In [11]:
# trajectories = replay_buffer.gather_all()
# total_loss, _ = agent.train(experience=trajectories)
# replay_buffer.clear()

# https://www.mikulskibartosz.name/how-to-train-a-reinforcement-learning-agent-using-tensorflow-agents/
def train_agent():
    dataset = replay_buffer.as_dataset(
        sample_batch_size=100,
        num_steps=10
    )
    
    iterator = iter(dataset)
    
    loss = None
    for _ in range(10):
        trajectories, _ = next(iterator)
        loss = agent.train(experience=trajectories)
    
    print("Training loss:", loss.loss.numpy())
    return loss.loss.numpy()

In [15]:
# train agent 
for i in range(50):
    print('Iteration', i)
    collect_driver.run()
    print('Gathering trajectories...')
    trajectories = replay_buffer.gather_all()
    print('Replay buffer gather all', trajectories)
    total_loss, _ = agent.train(experience=trajectories)
    replay_buffer.clear()
    print('Total', total_loss)

Iteration 0
Observations in ActorNet tf.Tensor(
[[[ 0.         -0.42587212 -1.2093381  -1.1066072  -2.9669387
    0.          0.          1.2060769   0.          0.15988994
    0.          1.1103549   0.         -0.5383446  -0.3588906
   -0.7297873  -0.5830615  -1.0525551   2.66691     0.
   -0.15013991 -0.45707595 -0.5511859  -0.45919695  1.7543349
   -0.18913272 -0.52357084 -1.8185984   0.         -0.54478574
   -0.51913404  0.          0.         -0.36321494  0.
    0.          1.41234     0.         -0.24646446  0.        ]
  [ 0.          0.45192003  0.          4.788521   -0.28990066
    1.5055937   0.         -0.42523494  0.          0.
   -0.6324552  -0.19624195  0.         -0.13601542  0.
   -0.8373201  -1.1601118   3.1169424  -0.39664936 -1.3032991
   -0.36352918 -0.7056376   1.248919    0.8510008   0.
   -0.36349896 -1.7593246   3.3338575  -0.24245687  0.8703022
    1.3123169   0.639009    0.         -1.7593246  -0.6141761
    0.         -0.32545304  0.          0.27382016  

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.42587212 -1.2093381  -1.1066072  -2.9669387
     0.          0.          1.2060769   0.          0.15988994
     0.          1.1103549   0.         -0.5383446  -0.3588906
    -0.7297873  -0.5830615  -1.0525551   2.66691     0.
    -0.15013991 -0.45707595 -0.5511859  -0.45919695  1.7543349
    -0.18913272 -0.52357084 -1.8185984   0.         -0.54478574
    -0.51913404  0.          0.         -0.36321494  0.
     0.          1.41234     0.         -0.24646446  0.        ]
   [ 0.          0.45192003  0.          4.788521   -0.28990066
     1.5055937   0.         -0.42523494  0.          0.
    -0.6324552  -0.19624195  0.         -0.13601542  0.
    -0.8373201  -1.1601118   3.1169424  -0.39664936 -1.3032991
    -0.36352918 -0.7056376   1.248919    0.8510008   0.
    -0.36349896 -1.7593246   3.3338575  -0.24245687  0.8703022
     1.3123169   0.639009    0.         -1.7593246  -0.6141761
     0.         -0.32545304  0.          0.273820

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.42587212 -1.2093381  -1.1066072  -2.9669387
     0.          0.          1.2060769   0.          0.15988994
     0.          1.1103549   0.         -0.5383446  -0.3588906
    -0.7297873  -0.5830615  -1.0525551   2.66691     0.
    -0.15013991 -0.45707595 -0.5511859  -0.45919695  1.7543349
    -0.18913272 -0.52357084 -1.8185984   0.         -0.54478574
    -0.51913404  0.          0.         -0.36321494  0.
     0.          1.41234     0.         -0.24646446  0.        ]
   [ 0.          0.45192003  0.          4.788521   -0.28990066
     1.5055937   0.         -0.42523494  0.          0.
    -0.6324552  -0.19624195  0.         -0.13601542  0.
    -0.8373201  -1.1601118   3.1169424  -0.39664936 -1.3032991
    -0.36352918 -0.7056376   1.248919    0.8510008   0.
    -0.36349896 -1.7593246   3.3338575  -0.24245687  0.8703022
     1.3123169   0.639009    0.         -1.7593246  -0.6141761
     0.         -0.32545304  0.          0.273820

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.42587212 -1.2093381  -1.1066072  -2.9669387
     0.          0.          1.2060769   0.          0.15988994
     0.          1.1103549   0.         -0.5383446  -0.3588906
    -0.7297873  -0.5830615  -1.0525551   2.66691     0.
    -0.15013991 -0.45707595 -0.5511859  -0.45919695  1.7543349
    -0.18913272 -0.52357084 -1.8185984   0.         -0.54478574
    -0.51913404  0.          0.         -0.36321494  0.
     0.          1.41234     0.         -0.24646446  0.        ]
   [ 0.          0.45192003  0.          4.788521   -0.28990066
     1.5055937   0.         -0.42523494  0.          0.
    -0.6324552  -0.19624195  0.         -0.13601542  0.
    -0.8373201  -1.1601118   3.1169424  -0.39664936 -1.3032991
    -0.36352918 -0.7056376   1.248919    0.8510008   0.
    -0.36349896 -1.7593246   3.3338575  -0.24245687  0.8703022
     1.3123169   0.639009    0.         -1.7593246  -0.6141761
     0.         -0.32545304  0.          0.273820

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.42089003 -1.1802423  -1.0824871  -2.7086718
     0.          0.          1.1771469   0.          0.1582489
     0.          1.0860648   0.         -0.5314758  -0.35486618
    -0.7187498  -0.57533556 -1.0307889   2.4705467   0.
    -0.14860626 -0.4516011  -0.5440763  -0.4536876   1.6858523
    -0.18716055 -0.51696795 -1.7438384   0.         -0.5377968
    -0.51261115  0.          0.         -0.35913008  0.
     0.          1.3712847   0.         -0.24386498  0.        ]
   [ 0.          0.44652843  0.          3.9251776  -0.2867659
     1.4580098   0.         -0.4202627   0.          0.
    -0.6237066  -0.194187    0.         -0.13458821  0.
    -0.8232859  -1.1334862   2.8237684  -0.3920936  -1.2690312
    -0.3594399  -0.69520575  1.2177174   0.8365488   0.
    -0.3594101  -1.6903726  -0.32450768 -0.23988794  0.8552408
     1.2775195   0.6301205   0.         -1.6903726  -0.60581505
     0.         -0.32187176  0.          0.2708876

...

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.29062518 -0.65657765  1.0700088  -0.91306406
     1.8425937   0.         -0.9879973   0.         -1.0735487
    -0.17366843 -0.67110044  0.          1.9186931   2.5103402
     1.8721081  -0.38439322 -0.60299844 -0.87519515  0.
     2.0542274  -0.30987334 -0.36615625  2.513361   -0.7207996
    -0.6547061   2.5204537  -0.7980025   5.         -0.47936767
    -0.9280404   0.          5.          2.7735927   0.
     0.         -0.44637582  0.         -0.17268406  0.        ]
   [ 0.          0.3067193   0.         -0.40298405 -0.20165977
    -0.8384211   2.42621     2.726878   -0.20210889  0.
     2.2789023  -0.33156192  0.         -0.31349072  0.
    -0.623899   -0.64068925  1.3728976  -0.2718792  -0.68468994
    -0.5944334  -0.45058444 -0.78314835 -1.1255251   0.
     2.924832   -1.3579079  -0.22723013 -0.4669238   0.98643005
     1.8319421   0.8514081  -2.0892494  -1.1430846  -0.7042563
     0.         -0.7530863   0.         -1.1818

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.29062518 -0.65657765  1.0700088  -0.91306406
     1.8425937   0.         -0.9879973   0.         -1.0735487
    -0.17366843 -0.67110044  0.          1.9186931   2.5103402
     1.8721081  -0.38439322 -0.60299844 -0.87519515  0.
     2.0542274  -0.30987334 -0.36615625  2.513361   -0.7207996
    -0.6547061   2.5204537  -0.7980025   5.         -0.47936767
    -0.9280404   0.          5.          2.7735927   0.
     0.         -0.44637582  0.         -0.17268406  0.        ]
   [ 0.          0.3067193   0.         -0.40298405 -0.20165977
    -0.8384211   2.42621     2.726878   -0.20210889  0.
     2.2789023  -0.33156192  0.         -0.31349072  0.
    -0.623899   -0.64068925  1.3728976  -0.2718792  -0.68468994
    -0.5944334  -0.45058444 -0.78314835 -1.1255251   0.
     2.924832   -1.3579079  -0.22723013 -0.4669238   0.98643005
     1.8319421   0.8514081  -2.0892494  -1.1430846  -0.7042563
     0.         -0.7530863   0.         -1.1818

Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.28901437 -0.6518068   1.0584054  -0.904584
    -0.5454207   0.         -0.9781161   0.         -1.0618668
    -0.17273416 -0.6661582   0.          1.8740487   2.4209046
     1.8301389  -0.3821426  -0.5988208  -0.86736315  0.
     2.0011344  -0.3081355  -0.36403677  2.4236412  -0.7152408
    -0.64995617  2.4300647  -0.79137874  5.         -0.47636747
    -0.9192925   0.          5.          2.657103    0.
     0.         -0.44365156  0.         -0.1717679   0.        ]
   [ 0.          0.30500245  0.         -0.40059552 -0.2005721
    -0.8311833   2.3444479   2.615538   -0.20101851  0.
     2.209495   -0.32968044  0.         -0.31172863  0.
    -0.61949587 -0.63610023  1.352968   -0.27038068 -0.67958444
    -0.5903452  -0.4478256  -0.7767401  -1.1126361   0.
     2.790626   -1.3384707  -0.22599721 -0.4640285   0.9765799
     1.7921878   0.8439654  -2.033806   -1.1297679  -0.6989085
     0.         -0.7470986   0.         -1.1675731 

Output of neural network for action <tensorflow.python.keras.layers.core.Dense object at 0x7efc081eebd0> [[1.0366623 1.2717732 1.1851196 0.        0.       ]]
Observations in ActorNet tf.Tensor(
[[[[ 0.         -0.28901437 -0.6518068   1.0584054  -0.904584
    -0.5454207   0.         -0.9781161   0.         -1.0618668
    -0.17273416 -0.6661582   0.          1.8740487   2.4209046
     1.8301389  -0.3821426  -0.5988208  -0.86736315  0.
     2.0011344  -0.3081355  -0.36403677  2.4236412  -0.7152408
    -0.64995617  2.4300647  -0.79137874  5.         -0.47636747
    -0.9192925   0.          5.          2.657103    0.
     0.         -0.44365156  0.         -0.1717679   0.        ]
   [ 0.          0.30500245  0.         -0.40059552 -0.2005721
    -0.8311833   2.3444479   2.615538   -0.20101851  0.
     2.209495   -0.32968044  0.         -0.31172863  0.
    -0.61949587 -0.63610023  1.352968   -0.27038068 -0.67958444
    -0.5903452  -0.4478256  -0.7767401  -1.1126361   0.
     2.790626   -1

Output of neural network for action <tensorflow.python.keras.layers.core.Flatten object at 0x7efc0824ea90> [[ 0.         -0.28901437 -0.6518068   1.0584054  -0.904584   -0.5454207
   0.         -0.9781161   0.         -1.0618668  -0.17273416 -0.6661582
   0.          1.8740487   2.4209046   1.8301389  -0.3821426  -0.5988208
  -0.86736315  0.          2.0011344  -0.3081355  -0.36403677  2.4236412
  -0.7152408  -0.64995617  2.4300647  -0.79137874  5.         -0.47636747
  -0.9192925   0.          5.          2.657103    0.          0.
  -0.44365156  0.         -0.1717679   0.          0.          0.30500245
   0.         -0.40059552 -0.2005721  -0.8311833   2.3444479   2.615538
  -0.20101851  0.          2.209495   -0.32968044  0.         -0.31172863
   0.         -0.61949587 -0.63610023  1.352968   -0.27038068 -0.67958444
  -0.5903452  -0.4478256  -0.7767401  -1.1126361   0.          2.790626
  -1.3384707  -0.22599721 -0.4640285   0.9765799   1.7921878   0.8439654
  -2.033806   -1.12976

In [ ]:
# see how agent performs 
time_step = tf_env.reset()
for _ in range(50):
    tf_env.reset()
    episode_reward = 0
    episode_steps = 0
    while not tf_env.current_time_step().is_last():
        action = agent.policy.action(tf_env.current_time_step()).action
        print('predicted action', action)
        next_time_step = tf_env.step(action)
        episode_steps += 1
        print("Reward", next_time_step.reward.numpy())
        episode_reward += next_time_step.reward.numpy()
    print("Steps:", episode_steps, "Reward:", episode_reward)

In [ ]:
dir(agent.collect_policy)

In [ ]:
agent.collect_policy._action_spec

In [ ]:
agent.collect_policy._policy_step_spec